In [1]:
import pandas as pd
from py2neo import Graph, Node
import time
import bson
from tabulate import tabulate

# Neo4j Database Construction

In [3]:
start_time = time.time()

In [1]:
!pip install pymongo

In [2]:
import bson

In [3]:
# load tweet data in bson format
bson_file = open('WDM1.bson', 'rb')
data = bson.decode_all(bson_file.read())
bson_file.close()

In [2]:
# connect to neo4j database
graph = Graph("bolt://localhost:7687", auth=("neo4j", "twitterdb"))

In [6]:
# Create sets to store unique tags, urls, tweets and users
unique_tags = set()
unique_urls = set()
unique_tweets = set()
unique_users = set()

# Iterate over the different tweet data and add hashtag, url, tweet and user data to the sets
for item in data:

    # Get the tags from the tweets
    if 'entities' in item['includes']['tweets'][0] and 'hashtags' in item['includes']['tweets'][0]['entities']:
        hashtags = item['includes']['tweets'][0]['entities']['hashtags']
        for i in range(len(hashtags)):
            if 'tag' in hashtags[i]:
                tag = hashtags[i]['tag'].lower() #case insensitive
                unique_tags.add(tag)

    # Get the urls from the tweets
    if 'entities' in item['includes']['tweets'][0] and 'urls' in item['includes']['tweets'][0]['entities']:
        urls = item['includes']['tweets'][0]['entities']['urls']
        for i in range(len(urls)):
            if 'expanded_url' in urls[i]:
                unique_urls.add(urls[i]['expanded_url'])

    # Get tweet data
    tweet = dict()
    tweet["id"] =  item['includes']['tweets'][0]['id']  
    tweet["created_at"] = item['includes']['tweets'][0]['created_at']  
    tweet["author_id"] = item['includes']['tweets'][0]['author_id']
    if 'reply_count' in item['includes']['tweets'][0]['public_metrics']:
        tweet["reply_count"] = item['includes']['tweets'][0]['public_metrics']['reply_count']
    else:
        tweet["reply_count"] = "nan"        
    if 'referenced_tweets' in item['includes']['tweets'][0]:       
        tweet["type"] = item['includes']['tweets'][0]['referenced_tweets'][0]['type']   
    else:
        tweet["type"] = "nan"   
        
    unique_tweets.add(frozenset(tweet.items()))
    

    # Get the user data 
    user = dict()
    user["id"] = item['includes']['users'][0]['id']  
    user["username"] = item['includes']['users'][0]['username']  
    if 'followers_count' in item['includes']['users'][0]['public_metrics']:
        user["followers_count"] = item['includes']['users'][0]['public_metrics']['followers_count']    
    else:
        user["followers_count"] = "nan"
        
    unique_users.add(frozenset(user.items()))

### Node creation

In [7]:
# Create a node for each hashtag. The only node property is tag.
for tag in unique_tags:
    node = Node("Hashtag", tag=tag)
    graph.merge(node, "Hashtag", "tag")

In [8]:
# Create a node for each url. The only node property is url.
for url in unique_urls:
    node = Node("Link", url=url)
    graph.merge(node, "Link", "url")

In [9]:
# Create a node for each tweet. Node tweet properties are id, created_at, reply_count, type and author_id.
for tweet in unique_tweets:
    tweet_dict = dict(tweet)
    node = Node("Tweet", id=tweet_dict["id"], created_at=tweet_dict["created_at"], reply_count=tweet_dict["reply_count"]
                , type=tweet_dict["type"], author_id=tweet_dict["author_id"])
    graph.merge(node, "Tweet", "id")

In [10]:
# Create a node for each user. Node user properties are id, username and followers_count.
for user in unique_users:
    user_dict = dict(user)
    node = Node("User", id=user_dict["id"], username=user_dict["username"], followers_count=user_dict["followers_count"])
    graph.merge(node, "User", "id")

### Relationships creation

In [11]:
print("User - TWEETED - Tweet")
graph.run("MATCH (u: User),(t: Tweet) WHERE u.id = t.author_id and t.type<> 'retweeted' and t.type<> 'quoted' and t.type<> 'replied_to' MERGE (u)-[r:TWEETED]->(t) return count(r)")

tweet begin


count(r) 
----------
     8477

In [12]:
print("User - RETWEETED - Tweet")
graph.run("MATCH (u: User),(t: Tweet) WHERE u.id = t.author_id and t.type = 'retweeted' MERGE (u)-[r:RETWEETED]->(t) return count(r)")

retweet begin


count(r) 
----------
    22887

In [13]:
print("User - QUOTED - Tweet")
graph.run("MATCH (u: User),(t: Tweet) WHERE u.id = t.author_id and t.type = 'quoted' MERGE (u)-[r:QUOTED]->(t) return count(r)")

quote begin


count(r) 
----------
      749

In [14]:
print("User - REPLIED_TO - Tweet")
graph.run("MATCH (u: User),(t: Tweet) WHERE u.id = t.author_id and t.type = 'replied_to' MERGE (u)-[r:REPLIED_TO]->(t) return count(r)")

reply begin


count(r) 
----------
     1110

In [15]:
# Iterate over the different tweet data to create relationships between nodes
for item in data:

    # Get the tweets
    tweet = {}
    tweet["id"] = item['includes']['tweets'][0]['id']  
    tweet["author_id"] = item['includes']['tweets'][0]['author_id']  

    if all(tweet.values()) and not all(pd.isna(v) and  pd.isnull(v) and v != "nan" for v in tweet.values()):  # only add non-empty and non-nan tweets
        if 'entities' in item['includes']['tweets'][0] and 'hashtags' in item['includes']['tweets'][0]['entities']:
            hashtags = item['includes']['tweets'][0]['entities']['hashtags']
            for i in range(len(hashtags)):
                if 'tag' in hashtags[i]:
                    tag = hashtags[i]['tag'].lower()
                    # Tweet - HAS_HASHTAG - Hashtag
                    tagRelTweet = graph.run("MATCH (t: Tweet),(h: Hashtag) WHERE h.tag = $tag1 and t.id = $tweetId MERGE (t)-[r:HAS_HASHTAG]->(h) return count(r)",tag1 = tag, tweetId = tweet["id"]).data()
                    # User - USED_HASHTAG - Hashtag
                    tagRelUser = graph.run("MATCH (u: User),(h: Hashtag) WHERE h.tag = $tag1 and u.id = $userId MERGE (u)-[r:USED_HASHTAG]->(h) return count(r)",tag1 = tag, userId = tweet["author_id"]).data()
                     
        if 'entities' in item['includes']['tweets'][0] and 'urls' in item['includes']['tweets'][0]['entities']:
            urls = item['includes']['tweets'][0]['entities']['urls']
            for i in range(len(urls)):
                if 'expanded_url' in urls[i]:
                    url = urls[i]['expanded_url']
                    # Tweet - HAS_URL - Link
                    urlRelTweet = graph.run("MATCH (t: Tweet),(l: Link) WHERE l.url = $url1 and t.id = $tweetId MERGE (t)-[r:HAS_URL]->(l) return count(r)",url1 = url, tweetId = tweet["id"]).data()
                    # User - USED_URL - Link
                    urlReluser = graph.run("MATCH (u: User),(l: Link) WHERE l.url = $url1 and u.id = $userId MERGE (u)-[r:USED_URL]->(l) return count(r)",url1 = url, userId = tweet["author_id"]).data()
   
    # Get the users 
    user = {}
    user["id"] = item['includes']['users'][0]['id'] 

    if all(user.values()) and not all(pd.isna(v) and  pd.isnull(v) and v != "nan" for v in user.values()):  # only add non-empty and non-nan users
        
         if 'entities' in item['data'] and 'mentions' in item['data']['entities']:
            mentions = item['data']['entities']['mentions']
            for i in range(len(mentions)):
                if 'id' in mentions[i]:
                    mentions_id = mentions[i]['id']
                    mentions_username = mentions[i]['username']
                    # if user does not already exist in the network, add User node
                    userExists = graph.run("MATCH (u:User {id: $id1}) return count(u.id)",id1 = mentions_id).data()
                    if(userExists[0]["count(u.id)"] == 0):
                        node = Node("User", id=mentions_id, username=mentions_username)
                        graph.merge(node, "User", "id")  
                    # User - MENTIONS - User 
                    mentionRel = graph.run("MATCH (u1:User),(u2:User) WHERE u1.id = $user1Id and u2.id = $user2Id MERGE (u1)-[r:MENTIONS]->(u2) return count(r)",user1Id = user["id"], user2Id = mentions_id).data()    

In [16]:
end_time = time.time()  # set the end time
elapsed_time = end_time - start_time  # calculate the elapsed time
print(f"Elapsed time: {elapsed_time} seconds")

Elapsed time: 7147.115245580673 seconds


# Questions & Answers

### 1. Get the total number of tweets

In [17]:
query1 = graph.run("MATCH (t:Tweet) RETURN count(t) AS total_tweets")
print(query1)

 total_tweets 
--------------
        33223 



### 3. Get the total number of hashtags (case insensitive)

In [18]:
query3 = graph.run("MATCH (h:Hashtag) RETURN count(h) AS total_hashtags")
print(query3)

 total_hashtags 
----------------
          11404 



### 5. Get the 20 most popular URLs in descending order

In [8]:
query5 = graph.run("""
MATCH (:User)-[r:USED_URL]->(link:Link)
RETURN link.url AS url, COUNT(r) AS url_count
ORDER BY url_count DESC
LIMIT 20
""")

for record in query5:
    print(f"Url: {record['url']}, Url count: {record['url_count']}")

Url: https://twitter.com/conscientious1o/status/1612372707936718849/photo/1, Url count: 110
Url: https://twitter.com/UNESCO/status/1611136758325846017/photo/1, Url count: 77
Url: https://bit.ly/3WVRK58, Url count: 74
Url: https://twitter.com/iamojon_/status/1611795133153804288/photo/1, Url count: 54
Url: http://bit.ly/GreenITNvidia, Url count: 48
Url: https://twitter.com/Equal_Fights/status/1613791501787566080/video/1, Url count: 45
Url: https://twitter.com/Equal_Fights/status/1613813839870451713/video/1, Url count: 38
Url: https://twitter.com/Equal_Fights/status/1614119793879121920/video/1, Url count: 37
Url: https://twitter.com/Equal_Fights/status/1614680829552201729/video/1, Url count: 31
Url: https://twitter.com/CurieuxExplorer/status/1610547866195615749/video/1, Url count: 28
Url: https://doi.org/10.1515/jib-2019-0005, Url count: 28
Url: https://twitter.com/nammavar11/status/1609825527040475136/photo/1, Url count: 27
Url: https://doi.org/10.1017/qpb.2021.18, Url count: 26
Url: htt

### 7. Get the followers count of each user

In [22]:
query7 = graph.run("""
MATCH (u:User) 
WHERE u.followers_count is not null  
AND u.followers_count <> "nan"
RETURN u.username AS username, u.followers_count AS followers_count
ORDER BY u.followers_count DESC
""")

# convert the result to a list of lists
table = []
for record in query7:
    table.append([record['username'], record['followers_count']])

# print the table
print(tabulate(table, headers=['username', 'followers_count'], tablefmt='orgtbl'))

| username        |   followers_count |
|-----------------+-------------------|
| thekiranbedi    |          12185146 |
| UNHumanRights   |           4022080 |
| UNESCO          |           3675313 |
| UN_Women        |           2242549 |
| bsindia         |           2232593 |
| glamourmag      |           1302202 |
| ELLEINDIA       |           1235302 |
| CNBCTV18News    |           1089824 |
| BLACKPINKGLOBAL |           1000438 |
| khaleejtimes    |            974472 |
| UNGeneva        |            899576 |
| thebetterindia  |            796657 |
| iownjd          |            795479 |
| UN_News_Centre  |            709651 |
| OECD            |            694189 |
| MPTourism       |            642323 |
| threadreaderapp |            636172 |
| startupindia    |            590581 |
| unwomenindia    |            578258 |
| UNPeacekeeping  |            569547 |
| amitabhk87      |            566904 |
| skylarclouds    |            545827 |
| CarolNdosi      |            542696 |


### 9. Get the number of tweets & retweets per hour

In [19]:
query9 = graph.run("""
MATCH (u:User)-[:TWEETED]->(t:Tweet)
WHERE t.created_at IS NOT NULL
WITH datetime(t.created_at).hour AS hour, count(t) AS total_tweets
ORDER BY hour
WITH hour, total_tweets

MATCH (u:User)-[:RETWEETED]->(t:Tweet)
WHERE t.created_at IS NOT NULL
WITH hour, total_tweets, datetime(t.created_at).hour AS retweet_hour, count(t) AS total_retweets
WHERE hour = retweet_hour
RETURN hour, total_tweets, total_retweets, (total_tweets + total_retweets) AS total
ORDER BY hour
""")

table = []
for record in query9:
    table.append([record['hour'], record['total_tweets'], record['total_retweets'], record['total']])

# print the table
print(tabulate(table, headers=['hour', 'total_tweets', 'total_retweets', 'total'], tablefmt='orgtbl'))

|   hour |   total_tweets |   total_retweets |   total |
|--------+----------------+------------------+---------|
|      0 |            258 |              743 |    1001 |
|      1 |            192 |              673 |     865 |
|      2 |            193 |              588 |     781 |
|      3 |            274 |              732 |    1006 |
|      4 |            228 |              708 |     936 |
|      5 |            276 |              729 |    1005 |
|      6 |            303 |              838 |    1141 |
|      7 |            304 |              807 |    1111 |
|      8 |            362 |              924 |    1286 |
|      9 |            291 |              943 |    1234 |
|     10 |            356 |             1004 |    1360 |
|     11 |            370 |             1138 |    1508 |
|     12 |            434 |             1137 |    1571 |
|     13 |            470 |             1214 |    1684 |
|     14 |            550 |             1260 |    1810 |
|     15 |            612 |    

### 11. Get the user with the most replies

In [9]:
query11 = graph.run("""
MATCH (u:User)-[r:REPLIED_TO]->(t:Tweet) 
RETURN u.username , count(r) as reply_count
ORDER BY count(r) DESC LIMIT 1
""")

print(query11)

 u.username  | reply_count 
-------------|-------------
 FatmaHasimm |          54 



### 13. Get the top-20 hashtags that co-occur with the hashtag that has been used the most

In [26]:
query13 = graph.run("""
MATCH (:Tweet)-[r1:HAS_HASHTAG]->(h1:Hashtag)
WITH h1, COUNT(r1) AS count
ORDER BY count DESC
LIMIT 1

MATCH (h1)<-[r1:HAS_HASHTAG]-(:Tweet)-[r2:HAS_HASHTAG]->(h2:Hashtag)
WHERE h1 <> h2
WITH h1, h2, COUNT(r2) AS co_occur_count
ORDER BY co_occur_count DESC
LIMIT 20
RETURN h1.tag AS most_popular_hashtag, collect({hashtag: h2.tag, co_occur_count: co_occur_count}) AS top20_list
""")


for record in query13:
    print(f"Most popular hashtag: #{record['most_popular_hashtag']}")
    print(f"\nTop-20 hashtags that co-occur with hashtag #{record['most_popular_hashtag']}:")
    print(record['top20_list'])

Most popular hashtag: #womenintech

Top-20 hashtags that co-occur with hashtag #womenintech:
[{'co_occur_count': 1042, 'hashtag': '100daysofcode'}, {'co_occur_count': 1009, 'hashtag': 'womenwhocode'}, {'co_occur_count': 705, 'hashtag': 'coding'}, {'co_occur_count': 700, 'hashtag': 'python'}, {'co_occur_count': 693, 'hashtag': 'tech'}, {'co_occur_count': 673, 'hashtag': 'programming'}, {'co_occur_count': 614, 'hashtag': 'javascript'}, {'co_occur_count': 484, 'hashtag': 'codenewbie'}, {'co_occur_count': 471, 'hashtag': 'technology'}, {'co_occur_count': 465, 'hashtag': 'blacktechtwitter'}, {'co_occur_count': 448, 'hashtag': '100devs'}, {'co_occur_count': 441, 'hashtag': 'womeninstem'}, {'co_occur_count': 434, 'hashtag': 'devcommunity'}, {'co_occur_count': 422, 'hashtag': 'ai'}, {'co_occur_count': 269, 'hashtag': 'blockchain'}, {'co_occur_count': 262, 'hashtag': 'datascience'}, {'co_occur_count': 247, 'hashtag': 'techiewomen'}, {'co_occur_count': 236, 'hashtag': 'ces2023'}, {'co_occur_coun

### 15. Get the most “important” user in the dataset (use Graph algorithms: Pagerank, Betweenness centrality, etc.). You will apply these algorithms in the mention network (which includes retweets)

In [4]:
query15_1 = graph.run("""
CALL gds.graph.project.cypher(
    'mentionGraph',
    'MATCH (u:User) RETURN id(u) AS id',
    'MATCH (u:User)-[e:MENTIONS]->(m:User) 
     RETURN id(u) AS source, e.weight AS weight, id(m) AS target'
)
""")

### Pagerank

In [80]:
query15_2 = graph.run("""
CALL gds.pageRank.stream('mentionGraph') 
YIELD nodeId, score
RETURN gds.util.asNode(nodeId).username AS name, score
ORDER BY score DESC LIMIT 5
""")

first_user = query15_2.next()['name']

print("maxIterations = 20, dampingFactor = 0.85\n")
print(f"Most important user: {first_user}")
print("Next 4 most important users:")
print([usr['name'] for usr in query15_2])
 
    
# different pageRank parameters    
query15_3 = graph.run("""
CALL gds.pageRank.stream('mentionGraph', {
  maxIterations: 200,
  dampingFactor: 0.9
})
YIELD nodeId, score
RETURN gds.util.asNode(nodeId).username AS name, score
ORDER BY score DESC LIMIT 5
""")

first_user = query15_3.next()['name']

print("\n\nmaxIterations = 200, dampingFactor = 0.9\n")
print(f"Most important user: {first_user}")
print("Next 4 most important users:")
print([usr['name'] for usr in query15_3])  


maxIterations = 20, dampingFactor = 0.85

Most important user: crazydollsnft
Next 4 most important users:
['cryptosanthoshK', 'CatherineAdenle', 'GirlsWhoCode', 'conscientious1o']


maxIterations = 200, dampingFactor = 0.9

Most important user: crazydollsnft
Next 4 most important users:
['CatherineAdenle', 'cryptosanthoshK', 'CareerEmporium', 'conscientious1o']


### 17. For the 5th most important user, get the list of hashtags and URLs that have been posted (if no hashtags or URLs - check another user e.g. 6th, 7th , etc..)

In [9]:
query17 = graph.run("""
CALL gds.pageRank.stream('mentionGraph') 
YIELD nodeId, score
WITH gds.util.asNode(nodeId).username AS name, score
ORDER BY score DESC SKIP 4
LIMIT 1

MATCH (urls:Link)<-[:USED_URL]-(u:User {username: name})-[:USED_HASHTAG]->(h:Hashtag)
RETURN name AS username, collect(DISTINCT urls.url) AS urls, collect(DISTINCT h.tag) AS hashtags
""")

for record in query17:
    print(f"5th most important user: {record['username']}")
    print(f"urls: {record['urls']}\nhashtags: {record['hashtags']}")


5th most important user: conscientious1o
urls: ['https://twitter.com/conscientious1o/status/1612372707936718849/photo/1']
hashtags: ['unitedkingdom', 'womenempowerment']


### 19. Get the user communities that have been created based on the users’ interactions and visualise them (Louvain algorithm)

In [16]:
query19 = graph.run("""
CALL gds.louvain.write(
  'mentionGraph',
  {
    writeProperty: 'communityId'
  }
)
""")

In [22]:
query19 = graph.run("""
MATCH (u1:User)-[r:MENTIONS]->(:User) return u1.communityId as community, u1 as user order by community
""")

for record in query19:
    print(f"community id: {record['community']}")
    print(f"user: {record['user']}")
    


community id: 8
user: (_62573:User {communityId: 8, followers_count: 327, id: '329045084', username: 'rvickywarrior'})
community id: 11
user: (_63607:User {communityId: 11, followers_count: 20, id: '1063113278308737026', username: 'marradok'})
community id: 11
user: (_74900:User {communityId: 11, followers_count: 82, id: '1435287782147215370', username: 'CheetoVon3'})
community id: 13
user: (_66268:User {communityId: 13, followers_count: 1693, id: '86442998', username: 'Dm1one'})
community id: 17
user: (_66239:User {communityId: 17, followers_count: 2846, id: '1062818191309709315', username: 'errandboyFL'})
community id: 19
user: (_69525:User {communityId: 19, followers_count: 1131, id: '337261405', username: 'FaredaVandeKaap'})
community id: 24
user: (_60805:User {communityId: 24, followers_count: 19, id: '1402679751689441287', username: 'e2ehiring'})
community id: 25
user: (_74814:User {communityId: 25, followers_count: 521, id: '1499792853303709698', username: 'Courage_jr1'})
commun

## Our query ideas

### Find the users who have used the most popular hashtag in their tweets and at the most popular tweet hour. 

### Vasia

In [39]:
query = graph.run("""
MATCH (:Tweet)-[r1:HAS_HASHTAG]->(h1:Hashtag)
WITH h1 AS most_popular_hashtag, COUNT(r1) AS count
ORDER BY count DESC
LIMIT 1

MATCH (u:User)-[:TWEETED]->(t:Tweet)
WHERE t.created_at IS NOT NULL
WITH datetime(t.created_at).hour AS most_popular_hour, count(t) AS total_tweets, most_popular_hashtag
ORDER BY total_tweets DESC
LIMIT 1

MATCH (u:User)-[:TWEETED]->(t:Tweet)-[:HAS_HASHTAG]->(h:Hashtag)
WHERE h.tag = most_popular_hashtag.tag AND datetime(t.created_at).hour = most_popular_hour
RETURN u.username AS username, COUNT(t) AS num_tweets, most_popular_hashtag.tag as most_popular_hashtag, most_popular_hour
ORDER BY num_tweets DESC
""")

table = []
for record in query:
    table.append([record['username'], record['num_tweets']])

# print the table
print(tabulate(table, headers=['username', 'num_tweets'], tablefmt='orgtbl'))



| username        |   num_tweets |
|-----------------+--------------|
| bcsn_official   |           39 |
| techwomenuk     |           14 |
| WeSabio         |            8 |
| CourseOp        |            7 |
| Mayassignment   |            5 |
| WomenTechNet    |            5 |
| ColbournePoppy  |            4 |
| WomenCyberjutsu |            3 |
| NCAR_CISL       |            3 |
| AshfieldIct     |            3 |
| LDNTechWeek     |            2 |
| BCISharePoint   |            2 |
| parvezshahshaik |            2 |
| wisekidnetic    |            2 |
| CWRUWIT         |            2 |
| EQLHER          |            2 |
| cambsppug       |            2 |
| lkostova        |            2 |
| WomenTechSummit |            2 |
| Oluwaseunnfunmi |            2 |
| KaLaiWong       |            2 |
| Designer101bot  |            2 |
| technicallyreem |            2 |
| bakshi_mini     |            2 |
| TiffanyMMoore   |            2 |
| TeamCasper365   |            2 |
| SDEubank        | 

### Vasilis

### Get the top 10 users who have tweeted the highest number of tweets that contain at least one hashtag and one URL

In [11]:
query = graph.run("""
MATCH (u:User)-[:TWEETED]->(t:Tweet)-[:HAS_HASHTAG]->(h:Hashtag), (t)-[:HAS_URL]->(l:Link)
WITH u, count(DISTINCT t) AS numTweets
WHERE numTweets > 0
RETURN u.username as username, numTweets
ORDER BY numTweets DESC
LIMIT 10
""")

table = []
for record in query:
    table.append([record['username'], record['numTweets']])

# print the table
print(tabulate(table, headers=['username', 'numTweets'], tablefmt='orgtbl'))

| username      |   numTweets |
|---------------+-------------|
| bcsn_official |         445 |
| CourseOp      |         170 |
| Lemetellusthg |         142 |
| Mahsamoulavi  |         124 |
| Financedata1  |         124 |
| Global1Event  |         123 |
| WeSabio       |          98 |
| DipsLab3      |          83 |
| KerenaNicole  |          72 |
| VivianAaron5  |          71 |
